<a href="https://colab.research.google.com/github/urmzd/lepus-classifier/blob/main/experiment_LC_40.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!rm -rf /content/*
!git clone https://github.com/urmzd/lepus-classifier

Cloning into 'lepus-classifier'...
remote: Enumerating objects: 1446, done.
remote: Counting objects: 100% (1446/1446), done.
remote: Compressing objects: 100% (910/910), done.
remote: Total 1446 (delta 835), reused 959 (delta 429), pack-reused 0
Receiving objects: 100% (1446/1446), 60.08 MiB | 10.20 MiB/s, done.
Resolving deltas: 100% (835/835), done.


In [2]:
!pip install wandb pipetools loguru
!pip install pytorch-lightning
!pip install pyyaml==5.4.1

In [3]:
!wandb login

wandb: Currently logged in as: csci-4155-rabbit-classifier (use `wandb login --relogin` to force relogin)


In [4]:
import sys
SRC_PATH = "/content/lepus-classifier"
sys.path.insert(0, SRC_PATH)
print(sys.path)

['/content/lepus-classifier', '', '/content', '/env/python', '/usr/lib/python37.zip', '/usr/lib/python3.7', '/usr/lib/python3.7/lib-dynload', '/usr/local/lib/python3.7/dist-packages', '/usr/lib/python3/dist-packages', '/usr/local/lib/python3.7/dist-packages/IPython/extensions', '/root/.ipython']


In [5]:
from src.bootstrap import bootstrap, TrainerFactory, N_CLASSES
from src.data.data_handler import BaseModel, MetricsCallback
from pathlib import Path
from pytorch_lightning.loggers import WandbLogger
import wandb
import pytorch_lightning as pl
import torch
from torchmetrics import Accuracy
import torch.nn.functional as F
import math

/usr/local/lib/python3.7/dist-packages/distributed/config.py:20: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  defaults = yaml.load(f)


In [6]:
class BaseOptimModel(BaseModel):
  def __init__(self, n_targets=2, learning_rate=1e-5):
      super().__init__(n_targets=n_targets, learning_rate=learning_rate)
      self.layer1 = torch.nn.Conv2d(1, 20, 2, 2)
      self.layer2= torch.nn.MaxPool2d(2, 2)
      self.layer3=torch.nn.Conv2d(20, 200, 2)
      self.layer4=torch.nn.MaxPool2d(2, 2)
      self.layer5=torch.nn.Flatten(start_dim=1)
      self.layer6=torch.nn.ReLU()
      self.layer7=torch.nn.Linear(int(math.pow(24,2)) * 200, 2)
      self.layer8=torch.nn.LogSoftmax()
      super().__post_init__()

  def forward(self, x):
      res_1 = self.layer1(x)
      res_2 = self.layer2(res_1)
      res_3 = self.layer3(res_2)
      res_4 = self.layer4(res_3)
      res_5 = self.layer5(res_4)
      res_6 = self.layer6(res_5)
      res_7 = self.layer7(res_6)
      res_8 = self.layer8(res_7)
      return res_8

def get_trainer_factory():

  trainer_factory = TrainerFactory(
      strategy=None, 
      max_epochs=32, 
  )
  
  return trainer_factory

In [7]:
class AdaGradModel(BaseOptimModel):
    def configure_optimizers(self):
      return torch.optim.Adagrad(self.parameters(), self.learning_rate)

bootstrap(trainer_factory=get_trainer_factory(), data_manifest_path=Path("/content/lepus-classifier/resources/data.csv"), model=AdaGradModel(), logger_kwargs={
    "name": "AdaGrad"
})

Global seed set to 42
wandb: Currently logged in as: csci-4155-rabbit-classifier (use `wandb login --relogin` to force relogin)


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
wandb: logging graph, to disable use `wandb.watch(log_graph=False)`
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name   | Type       | Params
--------------------------------------
0 | layer1 | Conv2d     | 100   
1 | layer2 | MaxPool2d  | 0     
2 | layer3 | Conv2d     | 16.2 K
3 | layer4 | MaxPool2d  | 0     
4 | layer5 | Flatten    | 0     
5 | layer6 | ReLU       | 0     
6 | layer7 | Linear     | 230 K 
7 | layer8 | LogSoftmax | 0     
--------------------------------------
246 K     Trainable params
0         Non-trainable params
246 K     Total params
0.987     Total estimated model params size (MB)
2022-04-10 00:42:42.185 | INFO     | src.data.data_handler:on_advance_start:213 - STARTING FOLD # 0
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/data_connector.py:245: PossibleUserWarning: The dataloader, tra

Training: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:22: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.


Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

In [8]:
class SGDModel(BaseOptimModel):
    def __init__(self, momentum=0.99):
      self.momentum = momentum
      super().__init__()

    def configure_optimizers(self):
      return torch.optim.SGD(self.parameters(), self.learning_rate, momentum=self.momentum)
      
bootstrap(trainer_factory=get_trainer_factory(), data_manifest_path=Path("/content/lepus-classifier/resources/data.csv"), model=SGDModel(), logger_kwargs={
    "name": "SGD"
})

Global seed set to 42


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
wandb: logging graph, to disable use `wandb.watch(log_graph=False)`
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name   | Type       | Params
--------------------------------------
0 | layer1 | Conv2d     | 100   
1 | layer2 | MaxPool2d  | 0     
2 | layer3 | Conv2d     | 16.2 K
3 | layer4 | MaxPool2d  | 0     
4 | layer5 | Flatten    | 0     
5 | layer6 | ReLU       | 0     
6 | layer7 | Linear     | 230 K 
7 | layer8 | LogSoftmax | 0     
--------------------------------------
246 K     Trainable params
0         Non-trainable params
246 K     Total params
0.987     Total estimated model params size (MB)
2022-04-10 00:48:07.394 | INFO     | src.data.data_handler:on_advance_start:213 - STARTING FOLD # 0
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/data_connector.py:245: PossibleUserWarning:

The dataloader, tr

Training: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:22: UserWarning:

Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.



Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

In [9]:
class RMSpropModel(BaseOptimModel):
  def configure_optimizer(self):
    return torch.optim.RMSprop(self.parameters(), learning_rate=self.learning_rate)

bootstrap(trainer_factory=get_trainer_factory(), data_manifest_path=Path("/content/lepus-classifier/resources/data.csv"), model=RMSpropModel(), logger_kwargs={
    "name": "RMSprop"
})

Global seed set to 42


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
wandb: logging graph, to disable use `wandb.watch(log_graph=False)`
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name   | Type       | Params
--------------------------------------
0 | layer1 | Conv2d     | 100   
1 | layer2 | MaxPool2d  | 0     
2 | layer3 | Conv2d     | 16.2 K
3 | layer4 | MaxPool2d  | 0     
4 | layer5 | Flatten    | 0     
5 | layer6 | ReLU       | 0     
6 | layer7 | Linear     | 230 K 
7 | layer8 | LogSoftmax | 0     
--------------------------------------
246 K     Trainable params
0         Non-trainable params
246 K     Total params
0.987     Total estimated model params size (MB)
2022-04-10 00:53:43.407 | INFO     | src.data.data_handler:on_advance_start:213 - STARTING FOLD # 0
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/data_connector.py:245: PossibleUserWarning:

The dataloader, tr

Training: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:22: UserWarning:

Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.



Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

In [10]:
class AdamModel(BaseOptimModel):
  def configure_optimizer(self):
    return torch.optim.Adam(self.parameters(), learning_rate=self.learning_rate)

bootstrap(trainer_factory=get_trainer_factory(), data_manifest_path=Path("/content/lepus-classifier/resources/data.csv"), model=AdamModel(), logger_kwargs={
    "name": "Adam"
})

Global seed set to 42


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
wandb: logging graph, to disable use `wandb.watch(log_graph=False)`
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name   | Type       | Params
--------------------------------------
0 | layer1 | Conv2d     | 100   
1 | layer2 | MaxPool2d  | 0     
2 | layer3 | Conv2d     | 16.2 K
3 | layer4 | MaxPool2d  | 0     
4 | layer5 | Flatten    | 0     
5 | layer6 | ReLU       | 0     
6 | layer7 | Linear     | 230 K 
7 | layer8 | LogSoftmax | 0     
--------------------------------------
246 K     Trainable params
0         Non-trainable params
246 K     Total params
0.987     Total estimated model params size (MB)
2022-04-10 00:59:20.959 | INFO     | src.data.data_handler:on_advance_start:213 - STARTING FOLD # 0
/usr/local/lib/python3.7/dist-packages/pytorch_lightning/trainer/connectors/data_connector.py:245: PossibleUserWarning:

The dataloader, tr

Training: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:22: UserWarning:

Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.



Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]